In [17]:
library(ExperimentHub)
library(HDF5Array)
library(SummarizedExperiment)
eh <- ExperimentHub() 
setwd("/data/ExtraDisk/sdd/longzhilin/Data/drugData/CMAP_LINCS_2020")

snapshotDate(): 2020-10-27



In [18]:
query(eh, c("signatureSearchData", "lincs"))
lincs_path <- eh[["EH3226"]]
h5ls(lincs_path)
lincs <- SummarizedExperiment(HDF5Array(lincs_path, name="assay"))
lincs <- as.matrix(lincs@assays@data[[1]])
rownames(lincs) <- HDF5Array(lincs_path, name="rownames")[,1]
colnames(lincs) <- HDF5Array(lincs_path, name="colnames")[,1] #12328 x 45956
lincs

ExperimentHub with 4 records
# snapshotDate(): 2020-10-27
# $dataprovider: Broad Institute, DrugBank, Broad Institute, STITCH
# $species: Homo sapiens
# $rdataclass: character, list
# additional mcols(): taxonomyid, genome, description,
#   coordinate_1_based, maintainer, rdatadateadded, preparerclass, tags,
#   rdatapath, sourceurl, sourcetype 
# retrieve records with, e.g., 'object[["EH3226"]]' 

           title             
  EH3226 | lincs             
  EH3227 | lincs_expr        
  EH3228 | dtlink_db_clue_sti
  EH3233 | taurefList        

see ?signatureSearchData and browseVignettes('signatureSearchData') for documentation

loading from cache



group name     otype       dclass dim          
0 /     assay    H5I_DATASET FLOAT  12328 x 45956
1 /     colnames H5I_DATASET STRING 45956 x 1    
2 /     rownames H5I_DATASET STRING 12328 x 1

BRD-A03772856__CD34__trt_cp trichostatin-a__CD34__trt_cp
5720    0.36540002                 -1.9333                     
466     0.69385004                 -4.0653                     
6009    0.55435002                  0.1850                     
2309   -0.31579998                  2.2660                     
387     0.37180001                 -0.2558                     
3553    0.70824999                 -0.5149                     
427     0.18295000                 -1.6045                     
5898   -0.40434998                  3.5042                     
23365   0.49500000                  0.4630                     
6657   -0.58120000                  2.3181                     
5054   -0.25055000                 -0.2075                     
3108   -0.06060000                 -1.8116                     
1950    0.34324998                 -0.3875                     
351    -0.75015002                  0.0000                     
4846    0.44309998                  2.6904                     
1452    0.05585000                 -0.3123                     
4776   -0.92770004                  0.6834                     
6908    0.20305002                  1.6617                     
672     0.32475001                 -4.0764                     
5710    0.63964999                  0.2391                     
2115   -0.46765000                  2.5311                     
7015   -0.62810004                  2.9025                     
8726    0.46415001                 -3.4828                     
2185   -0.59829998                 -2.5377                     
3315   -0.22889999                 -1.1686                     
5289    0.04359999                  3.6465                     
868     0.10220000                  0.8592                     
1677   -0.20805000                  0.7930                     
7043   -0.27850002                  2.4205                     
5613   -0.66865003                  0.5340                     
⋮      ⋮                           ⋮                           
54552  -0.547550023                 0.5666                     
54920  -0.190850005                 2.6847                     
11178  -0.007799983                 1.4589                     
93643  -0.781599998                 0.9777                     
112869 -0.174050003                 0.1336                     
51147  -0.131500006                 2.5702                     
196403 -0.179949999                 3.3629                     
389677 -0.299800009                -1.7546                     
1296   -0.568499982                 4.0283                     
85352  -0.582249999                 2.8892                     
57610   0.498400003                 5.1220                     
27147  -0.202250004                 2.5838                     
79591   1.026950002                 2.7480                     
92595   0.652800024                -0.7214                     
51063   0.343500018                -0.8015                     
55223  -0.215350002                 4.3713                     
80022  -0.499350011                 3.3540                     
55589   0.989849985                -1.7614                     
376267 -0.697149992                 1.8690                     
84820  -0.152749985                 1.8001                     
2931   -0.489800006                 4.3996                     
63876  -0.252000004                 2.4605                     
51275  -0.829549968                 2.4557                     
158747 -0.933599949                 2.2661                     
283232 -0.549999952                 1.0838                     
25960   0.060000002                 1.8776                     
6376   -0.391449988                 2.0942                     
11033  -0.816999972                 0.0360                     
54869  -0.491949975                 3.9373                     
60     -0.487500012                -0.0225                     
       geldanamycin__CD34__trt_cp KUC10

In [31]:
#### load tumor-specific TFs
tumor.specific.TFs <- readRDS("/data/active_data/lzl/RenalTumor-20200713/DataAnalysis-20210803/scATAC/5.Motif/Analysis/tumor.specific.TFs.rds")
idx <- which(tumor.specific.TFs$Name %in% c("HOXC5", "VENTX", "ISL1", "OTP"))
tumor.specific.TFs <- tumor.specific.TFs[idx,]
#convert to entrez id
source(file = "/home/longzhilin/Analysis_Code/IDConvert.R")
gene.info <- IDConvert(tumor.specific.TFs$Name, method = "clusterProfiler", fromType = "SYMBOL", toType = "ENTREZID")
gene.info

'select()' returned 1:1 mapping between keys and columns



SYMBOL ENTREZID
1 VENTX  27287   
2 OTP    23440   
3 ISL1   3670    
4 HOXC5  3222

In [32]:
index <- match(gene.info$ENTREZID, rownames(lincs))
lincs.TF.matrix <- lincs[na.omit(index),]
rownames(lincs.TF.matrix) <- gene.info$SYMBOL[which(!is.na(index))]
lincs.TF.matrix
dim(lincs.TF.matrix)

BRD-A03772856__CD34__trt_cp trichostatin-a__CD34__trt_cp
VENTX -0.86745                    2.6854                      
ISL1  -0.18340                    0.0290                      
HOXC5 -0.59025                    3.2782                      
      geldanamycin__CD34__trt_cp KUC107191N__CD34__trt_cp
VENTX 2.93140                    0.31655                 
ISL1  2.10840                    0.86345                 
HOXC5 2.69445                    1.32265                 
      BRD-A35207501__CD34__trt_cp iloprost__CD34__trt_cp
VENTX 0.26720                     1.3062376             
ISL1  0.12125                     0.4669212             
HOXC5 0.61415                     2.0156755             
      BRD-A72498772__CD34__trt_cp BRD-A72796238__CD34__trt_cp
VENTX -0.37835                    0.5864                     
ISL1   0.60240                    1.9325                     
HOXC5 -0.21200                    1.0597                     
      BRD-A73513677__CD34__trt_cp BRD-A73558769__CD34__trt_cp ⋯
VENTX -0.19235                    -0.36255                    ⋯
ISL1   0.64980                    -0.45065                    ⋯
HOXC5 -0.46980                     0.28235                    ⋯
      MW-MITF24__MCF7__trt_cp l-buthionine-sulfoximine__PC3__trt_cp
VENTX 1.6858                  0.4772                               
ISL1  2.4253                  2.1372                               
HOXC5 1.1215                  0.7762                               
      alpha-tocopherol__PC3__trt_cp cisplatin__PC3__trt_cp
VENTX  0.6672                       0.4269                
ISL1  -2.3109                       0.4266                
HOXC5  0.2086                       0.1258                
      iniparib__PC3__trt_cp JMW-MITF1__PC3__trt_cp bortezomib__PC3__trt_cp
VENTX -0.6599               -0.7321                -0.5295                
ISL1  -0.1666                0.6976                -3.8550                
HOXC5 -0.5124                0.6798                -1.9251                
      selumetinib__PC3__trt_cp glutamine__PC3__trt_cp MW-MITF24__PC3__trt_cp
VENTX 0.8246                   -0.9867                 1.9501               
ISL1  1.1637                    0.0608                -0.5077               
HOXC5 0.6460                   -1.3305                 0.4147

[1]     3 45956

In [33]:
####screen the drug with decreased the TF's expression
drug.lists <- list()
for(i in 1:nrow(lincs.TF.matrix)){
    zscore <- lincs.TF.matrix[i,]
    info <- data.frame(drug = colnames(lincs.TF.matrix), zscore = zscore)
    sig.drug <- which(info$zscore < -2) 
    if(length(sig.drug)>0){
        sig.info <- info[sig.drug,]
    }else{
        sig.info <- NULL
    }
    drug.lists <- c(drug.lists, list(sig.info))
}
names(drug.lists) <- rownames(lincs.TF.matrix)
drug.lists

$VENTX
                                                                                       drug
butoconazole__HCC515__trt_cp                                   butoconazole__HCC515__trt_cp
amcinonide__VCAP__trt_cp                                           amcinonide__VCAP__trt_cp
verteporfin__VCAP__trt_cp                                         verteporfin__VCAP__trt_cp
napelline__HT29__trt_cp                                             napelline__HT29__trt_cp
clioquinol__HT29__trt_cp                                           clioquinol__HT29__trt_cp
NS-3694__VCAP__trt_cp                                                 NS-3694__VCAP__trt_cp
AS-605240__VCAP__trt_cp                                             AS-605240__VCAP__trt_cp
SJ-172550__VCAP__trt_cp                                             SJ-172550__VCAP__trt_cp
JAS07-005__VCAP__trt_cp                                             JAS07-005__VCAP__trt_cp
BRD-A38425832__MCF7__trt_cp                                     BRD-A38425832__MCF7__trt_cp
BRD-K32827536__PC3__trt_cp                                       BRD-K32827536__PC3__trt_cp
BRD-K48844671__PC3__trt_cp                                       BRD-K48844671__PC3__trt_cp
BRD-K23165181__VCAP__trt_cp                                     BRD-K23165181__VCAP__trt_cp
BRD-K58247702__VCAP__trt_cp                                     BRD-K58247702__VCAP__trt_cp
BRD-K70917163__VCAP__trt_cp                                     BRD-K70917163__VCAP__trt_cp
KU-C104140__A549__trt_cp                                           KU-C104140__A549__trt_cp
BRD-A11095214__MCF7__trt_cp                                     BRD-A11095214__MCF7__trt_cp
BRD-K33182644__MCF7__trt_cp                                     BRD-K33182644__MCF7__trt_cp
BRD-K98991361__A549__trt_cp                                     BRD-K98991361__A549__trt_cp
oxcarbazepine__MCF7__trt_cp                                     oxcarbazepine__MCF7__trt_cp
lansoprazole__VCAP__trt_cp                                       lansoprazole__VCAP__trt_cp
kitasamycin__VCAP__trt_cp                                         kitasamycin__VCAP__trt_cp
BRD-A16581344__A549__trt_cp                                     BRD-A16581344__A549__trt_cp
BRD-K88556033__A549__trt_cp                                     BRD-K88556033__A549__trt_cp
RAN-27__NEU__trt_cp                                                     RAN-27__NEU__trt_cp
BRD-K44893543__NEU__trt_cp                                       BRD-K44893543__NEU__trt_cp
BRD-K58279162__NEU__trt_cp                                       BRD-K58279162__NEU__trt_cp
BRD-K14316227__NPC__trt_cp                                       BRD-K14316227__NPC__trt_cp
treprostinil__PHH__trt_cp                                         treprostinil__PHH__trt_cp
BRD-K82971429__PHH__trt_cp                                       BRD-K82971429__PHH__trt_cp
BRD-K21672423__SKB__trt_cp                                       BRD-K21672423__SKB__trt_cp
BRD-K35568648__SKB__trt_cp                                       BRD-K35568648__SKB__trt_cp
BRD-K98731749__VCAP__trt_cp                                     BRD-K98731749__VCAP__trt_cp
BRD-K54159704__NEU__trt_cp                                       BRD-K54159704__NEU__trt_cp
BRD-A60386802__NPC__trt_cp                                       BRD-A60386802__NPC__trt_cp
BRD-K09460252__SKB__trt_cp                                       BRD-K09460252__SKB__trt_cp
BRD-A30083233__VCAP__trt_cp                                     BRD-A30083233__VCAP__trt_cp
BRD-A68274214__VCAP__trt_cp                                     BRD-A68274214__VCAP__trt_cp
BRD-K16180117__VCAP__trt_cp                                     BRD-K16180117__VCAP__trt_cp
parthenolide-(alternate-stereo)__VCAP__trt_cp parthenolide-(alternate-stereo)__VCAP__trt_cp
BRD-K47764688__VCAP__trt_cp                                     BRD-K47764688__VCAP__trt_cp
BRD-K52914903__VCAP__trt_cp                                     BRD-K52914903__VCAP__trt_cp
SEW-05685__VCAP__trt_cp              

In [7]:
#### which drug can target multiple TFs at the one experiment
multi.TFs <- sapply(drug.lists, function(x){
    return(rownames(x))
})
drugs <- unlist(multi.TFs)
sort(table(drugs),decreasing = T)

drugs
                  BRD-A30083233__VCAP__trt_cp 
                                            6 
parthenolide-(alternate-stereo)__VCAP__trt_cp 
                                            6 
                         BML-257__NEU__trt_cp 
                                            5 
                        tubacin__VCAP__trt_cp 
                                            5 
               1-phenylbiguanide__PHH__trt_cp 
                                            4 
                  BRD-A68274214__VCAP__trt_cp 
                                            4 
                  BRD-K25731886__A549__trt_cp 
                                            4 
                      genistein__VCAP__trt_cp 
                                            4 
              homoharringtonine__HA1E__trt_cp 
                                            4 
                    kitasamycin__VCAP__trt_cp 
                                            4 
                         LFM-A13__NEU__trt_cp 
       

In [34]:
####output 
library (plyr)
drug.result <- ldply (drug.lists, data.frame)
drug.result <- drug.result[,c(2,1,3)]
colnames(drug.result) <- c("Drug", "TF", "ZSCORE")
library(writexl)
drug.result$Drug.name <- gsub("__.*", "", drug.result$Drug)
drug.result$cellLine <- gsub("__trt_cp", "", drug.result$Drug)
drug.result$cellLine <- gsub(".*__", "", drug.result$cellLine)
drug.idx <- sort(table(drug.result$Drug.name),decreasing = T)
drug.result$Drug.name <- factor(drug.result$Drug.name, levels = names(drug.idx))
drug.result <- arrange(drug.result, Drug.name, TF, Drug)
write_xlsx(drug.result, "/data/active_data/lzl/RenalTumor-20200713/DataAnalysis-20210803/Drug/LINCS/lincs.TF.negative.drug.result.xlsx")
drug.result

Drug                                 TF    ZSCORE    Drug.name             
1   alpha-tocopherol__MCF7__trt_cp       ISL1  -2.502400 alpha-tocopherol      
2   alpha-tocopherol__PC3__trt_cp        ISL1  -2.310900 alpha-tocopherol      
3   anisomycin__NEU__trt_cp              HOXC5 -2.530992 anisomycin            
4   anisomycin__ASC__trt_cp              ISL1  -2.111786 anisomycin            
5   apicidin__HEPG2__trt_cp              HOXC5 -2.335700 apicidin              
6   apicidin__A375__trt_cp               ISL1  -2.681550 apicidin              
7   BG-1003__NEU__trt_cp                 ISL1  -2.279669 BG-1003               
8   BG-1003__NPC__trt_cp                 ISL1  -2.050464 BG-1003               
9   BG-1025__NEU__trt_cp                 ISL1  -2.330200 BG-1025               
10  BG-1025__NPC__trt_cp                 ISL1  -2.107575 BG-1025               
11  BML-257__NEU__trt_cp                 ISL1  -5.686600 BML-257               
12  BML-257__NEU__trt_cp                 VENTX -3.350300 BML-257               
13  BMY-14802__NPC__trt_cp               ISL1  -2.252357 BMY-14802             
14  BMY-14802__PHH__trt_cp               ISL1  -2.118578 BMY-14802             
15  BRD-A68274214__NEU__trt_cp           ISL1  -2.049750 BRD-A68274214         
16  BRD-A68274214__VCAP__trt_cp          VENTX -2.685372 BRD-A68274214         
17  BRD-K02223034__A549__trt_cp          ISL1  -2.238800 BRD-K02223034         
18  BRD-K02223034__SKB__trt_cp           ISL1  -2.220776 BRD-K02223034         
19  BRD-K25731886__A549__trt_cp          ISL1  -4.073600 BRD-K25731886         
20  BRD-K25731886__NEU__trt_cp           ISL1  -2.935900 BRD-K25731886         
21  BRD-K44893543__NEU__trt_cp           HOXC5 -2.403568 BRD-K44893543         
22  BRD-K44893543__NEU__trt_cp           VENTX -2.608974 BRD-K44893543         
23  BRD-K66884694__MCF7__trt_cp          ISL1  -2.475050 BRD-K66884694         
24  BRD-K66884694__VCAP__trt_cp          ISL1  -2.011937 BRD-K66884694         
25  BRD-K98731749__NEU__trt_cp           ISL1  -3.041465 BRD-K98731749         
26  BRD-K98731749__VCAP__trt_cp          VENTX -2.255098 BRD-K98731749         
27  butoconazole__PHH__trt_cp            ISL1  -2.217050 butoconazole          
28  butoconazole__HCC515__trt_cp         VENTX -2.043097 butoconazole          
29  cucurbitacin-i__MCF7__trt_cp         HOXC5 -2.504937 cucurbitacin-i        
30  cucurbitacin-i__MCF7__trt_cp         ISL1  -2.131572 cucurbitacin-i        
⋮   ⋮                                    ⋮     ⋮         ⋮                     
297 SEW-05685__VCAP__trt_cp              VENTX -2.412868 SEW-05685             
298 SJ-172550__VCAP__trt_cp              VENTX -2.893954 SJ-172550             
299 sorafenib__VCAP__trt_cp              HOXC5 -2.387828 sorafenib             
300 SQ-22536__NPC__trt_cp                HOXC5 -2.024650 SQ-22536              
301 SR-12813__NEU__trt_cp                ISL1  -2.061450 SR-12813              
302 ST-4029010__NEU__trt_cp              HOXC5 -2.160550 ST-4029010            
303 ST-638__HA1E__trt_cp                 ISL1  -2.139165 ST-638                
304 staurosporine__A375__trt_cp          ISL1  -3.507200 staurosporine         
305 STK-397047__NEU__trt_cp              ISL1  -2.067650 STK-397047            
306 STOCK1S-03920__MCF7__trt_cp          ISL1  -2.238906 STOCK1S-03920         
307 temozolomide__NEU__trt_cp            ISL1  -2.358148 temozolomide          
308 teniposide__NPC__trt_cp              ISL1  -2.629349 teniposide            
309 tert-butylhydroquinone__MCF7__trt_cp ISL1  -3.080953 tert-butylhydroquinone
310 toremifene__MCF7__trt_cp             HOXC5 -2.111762 toremifene            
311 torin-2__PHH__trt_cp                 ISL1  -2.098830 torin-2               
312 tranilast__PHH__trt_cp               ISL1  -3.020363 tranilast             
313 treprostinil__PHH__trt_cp            VENTX -2.756694 treprostinil          
314 tributyltin__HA1E__trt_cp            ISL1  -3.094550 tributyltin           
315 

##### 查看Lincs中的药物信息和细胞系信息

In [35]:
####drug information
siginfo_beta <- read.table(file = "siginfo_beta.txt", header = T, stringsAsFactors = F, sep = "\t")
head(siginfo_beta)

bead_batch nearest_dose pert_dose pert_dose_unit pert_idose pert_itime
1 b17          NA         100.0     ug/ml          100 ug/ml  336 h     
2 b15        10.0          10.0     uM             10 uM      3 h       
3 b15         2.5           2.5     uM             2.5 uM     24 h      
4 b18        10.0          10.0     uM             10 uM      3 h       
5 b15        10.0          10.0     uM             10 uM      3 h       
6 b15        10.0          10.0     uM             10 uM      24 h      
  pert_time pert_time_unit cell_mfc_name pert_mfc_id   ⋯
1 336       h              N8            BRD-U44432129 ⋯
2   3       h              A549          BRD-K81418486 ⋯
3  24       h              HT29          BRD-K70511574 ⋯
4   3       h              HME1          BRD-K81418486 ⋯
5   3       h              H1975         BRD-A61304759 ⋯
6  24       h              H1975         BRD-K85606544 ⋯
  sig_id                              pert_type cell_iname det_wells      
1 MET001_N8_XH:BRD-U44432129:100:336  trt_cp    NAMEC8     H05|H06|H07|H08
2 ABY001_A549_XH:BRD-K81418486:10:3   trt_cp    A549       L04|L08|L12    
3 ABY001_HT29_XH:BRD-K70511574:2.5:24 trt_cp    HT29       E18|E22        
4 LTC002_HME1_3H:BRD-K81418486:10     trt_cp    HME1       F19            
5 ABY001_H1975_XH:BRD-A61304759:10:3  trt_cp    H1975      P01|P05|P09    
6 ABY001_H1975_XH:BRD-K85606544:10:24 trt_cp    H1975      A15|A19|A23    
  det_plates            
1 MET001_N8_XH_X1_B17   
2 ABY001_A549_XH_X1_B15 
3 ABY001_HT29_XH_X1_B15 
4 LTC002_HME1_3H_X1_B18 
5 ABY001_H1975_XH_X1_B15
6 ABY001_H1975_XH_X1_B15
  distil_ids                                                                                     
1 MET001_N8_XH_X1_B17:H05|MET001_N8_XH_X1_B17:H06|MET001_N8_XH_X1_B17:H07|MET001_N8_XH_X1_B17:H08
2 ABY001_A549_XH_X1_B15:L04|ABY001_A549_XH_X1_B15:L08|ABY001_A549_XH_X1_B15:L12                  
3 ABY001_HT29_XH_X1_B15:E18|ABY001_HT29_XH_X1_B15:E22                                            
4 LTC002_HME1_3H_X1_B18:F19                                                                      
5 ABY001_H1975_XH_X1_B15:P01|ABY001_H1975_XH_X1_B15:P05|ABY001_H1975_XH_X1_B15:P09               
6 ABY001_H1975_XH_X1_B15:A15|ABY001_H1975_XH_X1_B15:A19|ABY001_H1975_XH_X1_B15:A23               
  build_name project_code cmap_name     is_ncs_exemplar
1 NA         MET          BRD-U44432129 0              
2 NA         ABY          vorinostat    0              
3 NA         ABY          HMN-214       0              
4 NA         LTC          vorinostat    0              
5 NA         ABY          tanespimycin  0              
6 NA         ABY          neratinib     0

In [36]:
cellinfo_beta <- read.table(file = "cellinfo_beta.modify.txt", header = T, stringsAsFactors = F, sep = "\t", comment.char = "!")
cellinfo_beta$cell_iname

[1] "1HAE"            "AALE"            "AG06263_2"       "AG06840_A"      
  [5] "AG078N1_1"       "C42"             "CD34"            "HAP1"           
  [9] "HEK293T"         "HIMG001"         "HIMG002"         "HME"            
 [13] "HMELZ"           "HPTEC"           "HS27A"           "HUES3"          
 [17] "HUH751"          "HUVEC"           "IPS-15-2"        "IPS-3"          
 [21] "IPS-ND34732"     "LHSAR"           "MCH58"           "MCLF0067SZ"     
 [25] "MCLF015CN"       "MCLF022CN"       "MCLF027CN"       "MCLF033SZ"      
 [29] "MCLF035SZ"       "MCLF037SZ"       "MCLF040SZ"       "MCLF051CN"      
 [33] "MCLF054CN"       "MCLF056CN"       "MCLF076SZ"       "MCLF100SZ"      
 [37] "MCLF117SZ"       "MCLF123SZ"       "MCLF126CN"       "MCLF130CN"      
 [41] "MCLF135CN"       "MCLF137CN"       "MCLF141SZ"       "MCLF162SZ"      
 [45] "MICROGLIA-PSEN1" "MNEU"            "NAMEC8"          "ND34732_7"      
 [49] "NKDBA"           "P1A82"           "P2X2B2"          "SKB"            
 [53] "WA09"            "XC.500"          "XC.L10"          "XC.L100"        
 [57] "XC.P026"         "XC.P031"         "XC.P033"         "XC.P091"        
 [61] "XC.P092"         "XC.P901"         "XC.P904"         "XC.P905"        
 [65] "XC.P906"         "XC.P907"         "XC.P908"         "XC.P909"        
 [69] "XC.P910"         "XC.P911"         "XC.P912"         "XC.P914"        
 [73] "XC.P915"         "XC.P922"         "XC.P930"         "XC.P931"        
 [77] "XC.P932"         "XC.P933"         "XC.P934"         "XC.P935"        
 [81] "XC.P936"         "XC.R10"          "HME1"            "BJAB"           
 [85] "HBL1"            "OCILY10"         "TMD8"            "TC32"           
 [89] "H1299"           "H1975"           "HCC515"          "SALE"           
 [93] "SHSY5Y"          "22RV1"           "HEC1A"           "NL20"           
 [97] "PHH"             "HA1E"            "HEK293"          "HEKTE"          
[101] "NEU"             "NPC"             "ASC"             "U266B1"         
[105] "HL60"            "K562"            "TF1"             "THP1"           
[109] "MINO"            "U937"            "A673"            "SKES1"          
[113] "U2OS"            "A549"            "HCC827"          "NCIH1437"       
[117] "NCIH1563"        "NCIH1573"        "NCIH1694"        "NCIH1781"       
[121] "NCIH1836"        "NCIH1975"        "NCIH2073"        "NCIH2110"       
[125] "NCIH2172"        "NCIH596"         "NCIH838"         "NCIH841"        
[129] "SKLU1"           "A375"            "SH4"             "SKMEL1"         
[133] "SKMEL28"         "SKMEL3"          "SKMEL5"          "LN229"          
[137] "DLD1"            "HCT116"          "HT29"            "LOVO"           
[141] "NCIH508"         "NCIH716"         "RKO"             "SW480"          
[145] "SW620"           "SW948"           "HEPG2"           "BT20"           
[149] "BT474"           "HS578T"          "MCF10A"          "MCF7"           
[153] "MDAMB231"        "MDAMB468"        "SKBR3"           "T47D"           
[157] "ZR751"           "G401"            "SKNSH"           "5637"           
[161] "J82"             "AGS"             "ES2"             "HELA"           
[165] "DU145"           "PC3"             "RWPE1"           "VCAP"           
[169] "A204"            "AN3CA"           "TOV112D"         "WI38"           
[173] "JURKAT"          "NALM6"           "PL21"            "OCILY19"        
[177] "SUDHL4"          "WSUDLCL2"        "BEN"             "DV90"           
[181] "HCC15"           "HCC44"           "IGR37"           "MELHO"          
[185] "CL34"            "BC3C"            "CAL29"           "VMCUB1"         
[189] "EFO27"           "LNCAP"           "YAPC"            "MFE319"         
[193] "OC314"           "OC316"           "HFL1"            "IMR90"          
[197] "HCC1588"         "HCC95"           "SNU1040"         "SNU407"         
[201] "SNUC4"           "SNUC5"           "CORL23"          "GP2D"           
[205] "HT115"           

In [37]:
#kidney cell line
index <- grep("kidney", cellinfo_beta$primary_disease)
cellinfo_beta[index,]

cell_iname cellosaurus_id donor_age donor_age_death donor_disease_age_onset
98  HA1E                                NA              NA                     
99  HEK293     CVCL_0045                NA              NA                     
100 HEKTE                               NA              NA                     
158 G401       CVCL_0270      3 months  NA              NA                     
236 RCC10RGB   CVCL_1647                NA              NA                     
    doubling_time
98  60           
99  24           
100              
158 48           
236 108          
    growth_medium                                                                                                                                                                                                 
98  MEM-ALPHA (Invitrogen A1049001) supplemented with 10% v/v fetal bovine serum (Sigma F4135) and 1% 100X penicillin-streptomycin-glutamine (Invitrogen 10378-016)                                               
99  ATCC-formulated Eagles Minimum Essential Medium, Catalog No. 30-2003. To make the complete growth medium, add the following components to the base medium: fetal bovine serum to a final concentration of 10%.
100                                                                                                                                                                                                               
158 McCoys5A                                                                                                                                                                                                      
236 DMEM+ 1%FBS                                                                                                                                                                                                   
    provider_catalog_id feature_id cell_type donor_ethnicity donor_sex
98                                 normal    Unknown         Unknown  
99                                 normal    Unknown         F        
100                                normal    Unknown         Unknown  
158 CRL-1441            c-108      tumor     Caucasian       M        
236                     c-526      tumor     Unknown         M        
    donor_tumor_phase cell_lineage primary_disease     
98  Unknown           kidney       normal kidney sample
99  Unknown           kidney       normal kidney sample
100 Unknown           kidney       normal kidney sample
158 Primary           soft_tissue  kidney cancer       
236 Unknown           kidney       kidney cancer       
    subtype                        provider_name growth_pattern
98  normal kidney sample                         unknown       
99  normal embryonal kidney sample               adherent      
100 normal kidney sample                         unknown       
158 carcinoma                      ATCC          adherent      
236 carcinoma                      RIKEN         adherent      
    ccle_name        cell_alias 
98  HA1E_KIDNEY                 
99                   293        
100 HEKTE_KIDNEY     HEK TE     
158 G401_SOFT_TISSUE G 401|G-401
236 RCC10RGB_KIDNEY  10RGB

In [38]:
#Engineered Kidney --- HA1E, HA1E,HK2
#kidney; Embryo --- HEK293T
RCCl.cellLines <- c("769P", "786O", "A704", "A498", "ACHN", "CaKi", "HEK293", "RCC", "HEKTE", "HA1E", "G401", "RCC10RGB")
RCC.drug.results <- sapply(RCCl.cellLines, function(x){
    index <- grep(x, drug.result$Drug)
    if(length(index)>0){
        return(drug.result[index,])
    }else{
        return(NULL)
    }
})
RCC.drug.results

$`769P`
NULL

$`786O`
NULL

$A704
NULL

$A498
NULL

$ACHN
NULL

$CaKi
NULL

$HEK293
NULL

$RCC
NULL

$HEKTE
NULL

$HA1E
                                    Drug    TF    ZSCORE              Drug.name
67  aminomethyltransferase__HA1E__trt_cp HOXC5 -2.349426 aminomethyltransferase
72              anagrelide__HA1E__trt_cp  ISL1 -2.888882             anagrelide
74                 ARP-101__HA1E__trt_cp HOXC5 -2.420850                ARP-101
76                     AVA__HA1E__trt_cp VENTX -2.028199                    AVA
101          BRD-A51929314__HA1E__trt_cp  ISL1 -2.227154          BRD-A51929314
117          BRD-K05402890__HA1E__trt_cp  ISL1 -2.309873          BRD-K05402890
231      homoharringtonine__HA1E__trt_cp HOXC5 -2.545411      homoharringtonine
282                R-59022__HA1E__trt_cp HOXC5 -2.440392                R-59022
303                 ST-638__HA1E__trt_cp  ISL1 -2.139165                 ST-638
314            tributyltin__HA1E__trt_cp  ISL1 -3.094550            tributyltin
315          triphenyl-tin__HA1E__trt_cp  ISL1 -2.005953          triphenyl-tin
    cellLine
67      HA1E
72      HA1E
74      HA1E
76      HA1E
101     HA1E
117     HA1E
231     HA1E
282     HA1E
303     HA1E
314     HA1E
315     HA1E

$G401
NULL

$RCC10RGB
NULL

In [39]:
####output
RCC.drug.result <- rbind(RCC.drug.results[[7]], RCC.drug.results[[10]])
library (plyr)
library(writexl)
drug.idx <- sort(table(RCC.drug.result$Drug),decreasing = T)
RCC.drug.result$Drug <- factor(RCC.drug.result$Drug, levels = names(drug.idx))
RCC.drug.result <- arrange(RCC.drug.result, Drug)
write_xlsx(RCC.drug.result, "/data/active_data/lzl/RenalTumor-20200713/DataAnalysis-20210803/Drug/LINCS/lincs.TF.RCC.negative.drug.result.xlsx")
RCC.drug.result

Drug                                 TF    ZSCORE    Drug.name             
1  aminomethyltransferase__HA1E__trt_cp HOXC5 -2.349426 aminomethyltransferase
2  anagrelide__HA1E__trt_cp             ISL1  -2.888882 anagrelide            
3  ARP-101__HA1E__trt_cp                HOXC5 -2.420850 ARP-101               
4  AVA__HA1E__trt_cp                    VENTX -2.028199 AVA                   
5  BRD-A51929314__HA1E__trt_cp          ISL1  -2.227154 BRD-A51929314         
6  BRD-K05402890__HA1E__trt_cp          ISL1  -2.309873 BRD-K05402890         
7  homoharringtonine__HA1E__trt_cp      HOXC5 -2.545411 homoharringtonine     
8  R-59022__HA1E__trt_cp                HOXC5 -2.440392 R-59022               
9  ST-638__HA1E__trt_cp                 ISL1  -2.139165 ST-638                
10 tributyltin__HA1E__trt_cp            ISL1  -3.094550 tributyltin           
11 triphenyl-tin__HA1E__trt_cp          ISL1  -2.005953 triphenyl-tin         
   cellLine
1  HA1E    
2  HA1E    
3  HA1E    
4  HA1E    
5  HA1E    
6  HA1E    
7  HA1E    
8  HA1E    
9  HA1E    
10 HA1E    
11 HA1E

In [40]:
####extract drug information
drug.RCC <- as.character(RCC.drug.result$Drug)
drug.RCC <- sapply(drug.RCC, function(x){
    a <- unlist(strsplit(x, "__"))
    return(a[1:2])
})
drug.RCC <- unique(t(drug.RCC))

idx <- apply(drug.RCC, 1, function(x){
    index <- which(siginfo_beta$cmap_name == x[1] & siginfo_beta$cell_iname == x[2])
    return(siginfo_beta[index, ])
})
drug..RCC.info <- ldply (idx, data.frame)
write_xlsx(drug..RCC.info, "/data/active_data/lzl/RenalTumor-20200713/DataAnalysis-20210803/Drug/LINCS/lincs.TF.RCC.drug.info.xlsx")
drug..RCC.info

.id                                  bead_batch nearest_dose pert_dose  
1  aminomethyltransferase__HA1E__trt_cp b3         10.000       10.00000000
2  aminomethyltransferase__HA1E__trt_cp b3         10.000       10.00000000
3  anagrelide__HA1E__trt_cp             b3         10.000       10.00000000
4  anagrelide__HA1E__trt_cp             f1b3       10.000       10.00000000
5  anagrelide__HA1E__trt_cp             b23         0.740        0.76923100
6  anagrelide__HA1E__trt_cp             b24         1.110        1.11111000
7  anagrelide__HA1E__trt_cp             b24         0.040        0.04115230
8  anagrelide__HA1E__trt_cp             b23         0.080        0.08547010
9  anagrelide__HA1E__trt_cp             b24        10.000       10.00000000
10 anagrelide__HA1E__trt_cp             b23         0.250        0.25641000
11 anagrelide__HA1E__trt_cp             b24         0.125        0.12345700
12 anagrelide__HA1E__trt_cp             b23         0.010        0.00949668
13 anagrelide__HA1E__trt_cp             b24         0.370        0.37037000
14 anagrelide__HA1E__trt_cp             b24         3.330        3.33333000
15 anagrelide__HA1E__trt_cp             b23         2.220        2.30769000
16 anagrelide__HA1E__trt_cp             b23         0.030        0.02849000
17 ARP-101__HA1E__trt_cp                b3         10.000       10.00000000
18 ARP-101__HA1E__trt_cp                b24         0.030        0.02849000
19 ARP-101__HA1E__trt_cp                b22         0.040        0.04115230
20 ARP-101__HA1E__trt_cp                b24         0.250        0.25641000
21 ARP-101__HA1E__trt_cp                b22         0.125        0.12345700
22 ARP-101__HA1E__trt_cp                b24         2.220        2.30769000
23 ARP-101__HA1E__trt_cp                b24         0.010        0.00949668
24 ARP-101__HA1E__trt_cp                b24         0.080        0.08547010
25 ARP-101__HA1E__trt_cp                b22        10.000       10.00000000
26 ARP-101__HA1E__trt_cp                b22         0.370        0.37037000
27 ARP-101__HA1E__trt_cp                b22         1.110        1.11111000
28 ARP-101__HA1E__trt_cp                b22         3.330        3.33333000
29 ARP-101__HA1E__trt_cp                b24         0.740        0.76923100
30 AVA__HA1E__trt_cp                    b13         3.330        3.33000000
31 AVA__HA1E__trt_cp                    b13         0.370        0.37000000
32 AVA__HA1E__trt_cp                    b13         1.110        1.11000000
33 AVA__HA1E__trt_cp                    b13         0.040        0.04000000
34 AVA__HA1E__trt_cp                    b13        10.000       10.00000000
35 AVA__HA1E__trt_cp                    b13         0.120        0.12000000
36 BRD-K05402890__HA1E__trt_cp          f1b3        0.370        0.35000000
37 BRD-K05402890__HA1E__trt_cp          b3         10.000       10.00000000
38 BRD-K05402890__HA1E__trt_cp          b3         10.000       10.00000000
39 BRD-K05402890__HA1E__trt_cp          b21         0.370        0.37037000
40 BRD-K05402890__HA1E__trt_cp          b21         0.125        0.12345700
41 BRD-K05402890__HA1E__trt_cp          b21         3.330        3.33333000
42 BRD-K05402890__HA1E__trt_cp          b21         1.110        1.11111000
43 BRD-K05402890__HA1E__trt_cp          b21        10.000       10.00000000
44 BRD-K05402890__HA1E__trt_cp          b21         0.040        0.04115230
45 R-59022__HA1E__trt_cp                b3         10.000       10.00000000
46 ST-638__HA1E__trt_cp                 b3         10.000       10.00000000
47 tributyltin__HA1E__trt_cp            f1b7       10.000       10.00000000
48 tributyltin__HA1E__trt_cp            f1b4       10.000       10.00000000
49 triphenyl-tin__HA1E__trt_cp          f1b7       10.000       10.00000000
50 triphenyl-tin__HA1E__trt_cp          f1b7       10.000       10.00000000
51 triphenyl-tin__HA1E__trt_cp          f1b4       10.000       10.00000000
52 triphenyl-tin__HA1E__trt_cp          f1b4       

In [41]:
####identify the candidate drugs with Z-score
mean.drug <- tapply(RCC.drug.result$ZSCORE, as.character(RCC.drug.result$Drug), mean)
mean.drug <- data.frame(Drug = names(mean.drug), mean.Zscore = mean.drug)
mean.drug <- mean.drug[order(mean.drug$mean.Zscore, decreasing = T),]
mean.drug

rankMean <- RCC.drug.result
rankMean$Drug <- factor(rankMean $Drug, levels = mean.drug$Drug)
rankMean <- arrange(rankMean, Drug)
write_xlsx(rankMean, "/data/active_data/lzl/RenalTumor-20200713/DataAnalysis-20210803/Drug/LINCS/lincs.TF.RCC.drug.meanRank.xlsx")

Drug                                
triphenyl-tin__HA1E__trt_cp          triphenyl-tin__HA1E__trt_cp         
AVA__HA1E__trt_cp                    AVA__HA1E__trt_cp                   
ST-638__HA1E__trt_cp                 ST-638__HA1E__trt_cp                
BRD-A51929314__HA1E__trt_cp          BRD-A51929314__HA1E__trt_cp         
BRD-K05402890__HA1E__trt_cp          BRD-K05402890__HA1E__trt_cp         
aminomethyltransferase__HA1E__trt_cp aminomethyltransferase__HA1E__trt_cp
ARP-101__HA1E__trt_cp                ARP-101__HA1E__trt_cp               
R-59022__HA1E__trt_cp                R-59022__HA1E__trt_cp               
homoharringtonine__HA1E__trt_cp      homoharringtonine__HA1E__trt_cp     
anagrelide__HA1E__trt_cp             anagrelide__HA1E__trt_cp            
tributyltin__HA1E__trt_cp            tributyltin__HA1E__trt_cp           
                                     mean.Zscore
triphenyl-tin__HA1E__trt_cp          -2.005953  
AVA__HA1E__trt_cp                    -2.028199  
ST-638__HA1E__trt_cp                 -2.139165  
BRD-A51929314__HA1E__trt_cp          -2.227154  
BRD-K05402890__HA1E__trt_cp          -2.309873  
aminomethyltransferase__HA1E__trt_cp -2.349426  
ARP-101__HA1E__trt_cp                -2.420850  
R-59022__HA1E__trt_cp                -2.440392  
homoharringtonine__HA1E__trt_cp      -2.545411  
anagrelide__HA1E__trt_cp             -2.888882  
tributyltin__HA1E__trt_cp            -3.094550

In [42]:
#### drug down-regulated the gene expression
negative.zscore <- RCC.drug.result[which(RCC.drug.result$ZSCORE<0),]
negative.zscore.mean <- tapply(negative.zscore$ZSCORE, as.character(negative.zscore$Drug), mean)
negative.zscore.mean <- data.frame(Drug = names(negative.zscore.mean), mean.Zscore = negative.zscore.mean)
negative.zscore.mean <- negative.zscore.mean[order(negative.zscore.mean$mean.Zscore),]
#negative.zscore.mean

negative.rankMean <- negative.zscore
negative.rankMean$Drug.name <- gsub("__.*", "", negative.rankMean$Drug)
idx <- names(sort(table(negative.rankMean$Drug.name), decreasing = T))
negative.rankMean$Drug.name <- factor(negative.rankMean$Drug.name, levels = idx)
negative.rankMean <- arrange(negative.rankMean, Drug.name)
write_xlsx(negative.rankMean, "/data/active_data/lzl/RenalTumor-20200713/DataAnalysis-20210803/Drug/LINCS/lincs.TF.RCC.drug.negative.rankMean.xlsx")
negative.rankMean

Drug                                 TF    ZSCORE    Drug.name             
1  aminomethyltransferase__HA1E__trt_cp HOXC5 -2.349426 aminomethyltransferase
2  anagrelide__HA1E__trt_cp             ISL1  -2.888882 anagrelide            
3  ARP-101__HA1E__trt_cp                HOXC5 -2.420850 ARP-101               
4  AVA__HA1E__trt_cp                    VENTX -2.028199 AVA                   
5  BRD-A51929314__HA1E__trt_cp          ISL1  -2.227154 BRD-A51929314         
6  BRD-K05402890__HA1E__trt_cp          ISL1  -2.309873 BRD-K05402890         
7  homoharringtonine__HA1E__trt_cp      HOXC5 -2.545411 homoharringtonine     
8  R-59022__HA1E__trt_cp                HOXC5 -2.440392 R-59022               
9  ST-638__HA1E__trt_cp                 ISL1  -2.139165 ST-638                
10 tributyltin__HA1E__trt_cp            ISL1  -3.094550 tributyltin           
11 triphenyl-tin__HA1E__trt_cp          ISL1  -2.005953 triphenyl-tin         
   cellLine
1  HA1E    
2  HA1E    
3  HA1E    
4  HA1E    
5  HA1E    
6  HA1E    
7  HA1E    
8  HA1E    
9  HA1E    
10 HA1E    
11 HA1E